# Proyecto I - Medidas de riesgo Var y CVaR

## Se importan las paqueterías necesarias

In [19]:
import datetime
import numpy as np
import pandas as pd
import yfinance as yf

from scipy.stats import norm, t

Se establece *plotly* como el motor de gráficas a utilizar

In [20]:
pd.options.plotting.backend = "plotly"

## Descarga y procesamiento de precios históricos para un ticker dado

### Descarga de datos históricos

In [21]:
def get_stock_prices(ticker, start_date, end_date):
    """Devuelve los precios de cierre de un activo, dados un ticker,
    una fecha de inicio y una fecha de fin.

    Parameters
    ----------
    ticker : str
        Ticket del activo.
    start_date : datetime.datetime
        Fecha de inicio.
    end_date : datetime.datetime
        Fecha de fin.

    Returns
    -------
    data : pandas.DataFrame
        Stock data.
    """
    
    data = yf.download(ticker, start=start_date, end=end_date)
    
    close_prices = data[["Close"]]
    close_prices.columns = [ticker]
    
    print(close_prices.head())
    
    return close_prices

Ticker a utilizar: [GCARSOA1.MX - Grupo Carso](https://finance.yahoo.com/quote/GCARSOA1.MX)

In [22]:
ticker = "GCARSOA1.MX"
start_date = datetime.datetime(2010, 1, 1)
end_date = datetime.datetime.now()

stock_prices = get_stock_prices(ticker, start_date, end_date)

[*********************100%%**********************]  1 of 1 completed
            GCARSOA1.MX
Date                   
2010-01-04    20.284569
2010-01-05    20.035229
2010-01-06    20.108562
2010-01-07    20.411682
2010-01-08    20.802805


#### Gráfica de histórico de precios de cierre

In [23]:
fig = stock_prices.plot(
    title="{} stock historic closing prices (2010-today)".format(ticker)
    )
fig.update_layout(yaxis_title="Price (USD)")

### Cálculo de retornos diarios

In [24]:
stock_returns = stock_prices.pct_change().dropna()

#### Gráfico de retornos diarios

In [25]:
fig = stock_returns.plot(
    title="{} historic daily returns (2010-today)".format(ticker)
    )
fig.update_layout(yaxis_title="Daily returns")

#### Histograma de retornos diarios

In [26]:
fig = stock_returns.hist(
    bins=50,
    title="{} Daily returns histogram (2010-today)".format(ticker),
    histnorm="probability density"
    )
fig.update_layout(xaxis_title="Daily returns")

#### Estadísticos descriptivos de los retornos diarios

In [27]:
stock_returns.describe()

GCARSOA1.MX
count  3473.000000
mean      0.000735
std       0.021462
min      -0.148936
25%      -0.011457
50%       0.000485
75%       0.012440
max       0.150008

#### Kurtosis

In [28]:
stock_returns.kurtosis()

GCARSOA1.MX    3.741893
dtype: float64

#### Sesgo

In [29]:
# Sesgo
stock_returns.skew()

GCARSOA1.MX    0.159481
dtype: float64

## Medidas de riesgo

### Definición de funciones para calcular las medidas de riesgo

#### VaR histórico

In [30]:
def VaR_historic(stock_returns, alpha):
    """Devuelve el VaR histórico para un nivel de confianza 1 - alpha.

    Parameters
    ----------
    stock_returns : pandas.DataFrame
        Retornos del activo.
    alpha : float
        Nivel de confianza: 1 - alpha.

    Returns
    -------
    VaR : float
        VaR histórico.
    """
    
    VaR = -stock_returns.quantile(alpha).values[0]
    
    return VaR

#### VaR paramétrico

In [31]:
def VaR_param(stock_returns, alpha, distribution):
    """Devuelve el VaR paramétrico para un nivel de confianza 1 - alpha,
    asumiendo una distribución normal o t de Student.

    Parameters
    ----------
    stock_returns : pandas.DataFrame
        Retornos del activo.
    alpha : float, optional
        Niivel de confianza: 1 - alpha.
    distribution : str
        Distribución a asumir: "normal" o "t".

    Returns
    -------
    VaR : float
        VaR paramétrico.
    """
    
    mean = stock_returns.mean()
    std = stock_returns.std()
    
    if distribution == "normal":
        VaR = -norm.ppf(alpha, mean, std)[0]
    elif distribution == "t":
        df = len(stock_returns) - 1
        VaR = -t.ppf(alpha, df, mean, std)[0]
    else:
        error_message = (
            "Distribución no soportada."
            " Opciones disponibles: 'normal' o 't'."
            )
        raise ValueError(error_message)
    return VaR

#### VaR por MonteCarlo

In [32]:
def VaR_MC(stock_returns, alpha, n_simulations=1000000):
    """Devuelve el VaR calculado por simulación Monte Carlo, asumiendo una
    distribución normal, para un nivel de confianza 1 - alpha, y un número
    de simulaciones 'n_simulations'.

    Parameters
    ----------
    stock_returns : pandas.DataFrame
        Retornos del activo.
    alpha : float
        Nivel de confianza: 1 - alpha.
    n_simulations : int, optional
        Número de simulaciones.

    Returns
    -------
    VaR : float
        VaR calculado por simulación Monte Carlo.
    """
    
    mean = stock_returns.mean()
    std = stock_returns.std()
    
    simulated_returns = np.random.normal(mean, std, n_simulations)
    
    VaR = -np.quantile(simulated_returns, alpha)
    
    return VaR


#### CVaR / Expected Shortfall histórico

In [33]:
def CVaR_historic(stock_returns, alpha):
    """Devuelve el CVaR histórico para un nivel de confianza 1 - alpha.

    Parameters
    ----------
    stock_returns : pandas.DataFrame
        Retornos del activo.
    alpha : float
        Nivel de confianza: 1 - alpha.

    Returns
    -------
    CVaR : float
        CVaR histórico.
    """
    
    VaR = VaR_historic(stock_returns, alpha)
    
    CVaR = -stock_returns[stock_returns <= -VaR].mean().values[0]
    
    return CVaR

#### VaR / Expected Shortfall paramétrico

In [34]:
def CVaR_param(stock_returns, alpha, dist):
    """Calcula el CVaR paramétrico, asumiendo una distribución normal o t de
    Student, para un nivel de confianza 1 - alpha.
    
    Parameters
    ----------
    stock_returns : pandas.DataFrame
        Retornos del activo.
    alpha : float
        Nivel de confianza: 1 - alpha.
    dist : str
        Distribución a asumir: "normal" o "t".
        
    Returns
    -------
    CVaR_param : float
        CVaR paramétrico.
    """
    
    VaR = VaR_param(stock_returns, alpha, dist)
    CVaR = -stock_returns[stock_returns <= -VaR].mean().values[0]
    return CVaR

#### CVaR / Expected Shortfall por MonteCarlo

In [35]:
def CVaR_MC(stock_returns, alpha, n_simulations=1000000):
    """Devuelve el CVaR calculado por simulación Monte Carlo, asumiendo una
    distribución normal, para un nivel de confianza 1 - alpha, y un número
    de simulaciones 'n_simulations'.
    
    Parameters
    ----------
    stock_returns : pandas.DataFrame
        Retornos del activo.
    alpha : float, optional
        Nivel de confianza: 1 - alpha.
    n_simulations : int, optional
        Número de simulaciones.
        
    Returns
    -------
    CVaR : float
        CVaR calculado por simulación Monte Carlo.
    """
    
    mean = stock_returns.mean()
    std = stock_returns.std()
    
    simulated_returns = np.random.normal(mean, std, n_simulations)
    
    VaR = -np.quantile(simulated_returns, alpha)
    
    CVaR = -simulated_returns[simulated_returns <= -VaR].mean()
    
    return CVaR

### Cálculo de medidas de riesgo sin ventanas móviles

#### Tabla comparativa

In [36]:
# Niveles de confianza: 1 - alpha
# alpha = 0.05 -> 95%
# alpha = 0.025 -> 97.5%
# alpha = 0.01 -> 99%

alphas = [0.05, 0.025, 0.01]

risk_dict = {
    "VaR histórico": [
        VaR_historic(
            stock_returns,
            alpha=alpha
            )
        for alpha in alphas
        ],
    "VaR paramétrico normal": [
        VaR_param(
            stock_returns,
            alpha=alpha,
            distribution="normal"
            )
        for alpha in alphas
        ],
    "VaR paramétrico t-student": [
        VaR_param(
            stock_returns,
            alpha=alpha,
            distribution="t"
            )
        for alpha in alphas
        ],
    "VaR Montecarlo": [
        VaR_MC(
            stock_returns,
            alpha=alpha
            )
        for alpha in alphas
        ],
    "CVaR histórico": [
        CVaR_historic(
            stock_returns,
            alpha=alpha
            )
        for alpha in alphas
        ],
    "CVaR paramétrico normal": [
        CVaR_param(
            stock_returns,
            alpha=alpha,
            dist="normal"
            )
        for alpha in alphas
        ],
    "CVaR paramétrico t-student": [
        CVaR_param(
            stock_returns,
            alpha=alpha,
            dist="t"
            )
        for alpha in alphas
        ],
    "CVaR Montecarlo": [
        CVaR_MC(
            stock_returns,
            alpha=alpha
            )
        for alpha in alphas
        ]
    }

index_names = [f"{(1-alpha)*100:.1f}%" for alpha in alphas]
risk_measures = pd.DataFrame(risk_dict, index=index_names)
risk_measures.index.name="Nivel de confianza"

risk_measures

VaR histórico  VaR paramétrico normal  \
Nivel de confianza                                          
95.0%                    0.033221                0.034567   
97.5%                    0.040294                0.041330   
99.0%                    0.051799                0.049193   

                    VaR paramétrico t-student  VaR Montecarlo  CVaR histórico  \
Nivel de confianza                                                              
95.0%                                0.034576        0.034602        0.045928   
97.5%                                0.041345        0.041276        0.055778   
99.0%                                0.049216        0.049349        0.071226   

                    CVaR paramétrico normal  CVaR paramétrico t-student  \
Nivel de confianza                                                        
95.0%                              0.048031                    0.048031   
97.5%                              0.057298                    0.057298   
99.0%                              0.065500                    0.065500   

                    CVaR Montecarlo  
Nivel de confianza                   
95.0%                      0.043547  
97.5%                      0.049435  
99.0%                      0.056423

#### Gráfica de barras de medidas de riesgo, agrupadas por nivel de confianza

In [37]:
risk_measures_percentage = risk_measures.apply(lambda x: x * 100).round(2)
fig = risk_measures_percentage.plot.bar(
    title=f"{ticker} - Medidas de riesgo, agrupadas por nivel de confianza",
    barmode='group'
    )
fig.update_layout(yaxis_title="Máxima pérdida esperada (%)")

#### Gráfica de barras de medidas de riesgo, agrupadas por definición de medida

In [38]:
fig = risk_measures_percentage.T.plot.bar(
    title=f"{ticker} - Medidas de riesgo a distintos niveles de confianza",
    barmode='group'
    )
fig.update_layout(yaxis_title="Máxima pérdida esperada (%)")

### Cálculo de medidas de riesgo usando ventanas móviles de 252 días bursátiles

#### Tabla comparativa

In [39]:
# Nivel de confianza: 1 - alpha
# alpha = 0.05 -> 95%
# alpha = 0.01 -> 99%

rolling_alphas = [0.05, 0.01]

window_size = 252

VaR_hist_series = [
    stock_returns.rolling(window_size).apply(
    lambda x: VaR_historic(pd.DataFrame(x), alpha=alpha)
    ) for alpha in rolling_alphas
                   ]

VaR_param_series = [
    stock_returns.rolling(window_size).apply(
        lambda x: VaR_param(pd.DataFrame(x), alpha=alpha, distribution="normal")
        ) for alpha in rolling_alphas
    ]

CVaR_hist_series = [
    stock_returns.rolling(window_size).apply(
    lambda x: CVaR_historic(pd.DataFrame(x), alpha=alpha)
    ) for alpha in rolling_alphas
                   ]

CVaR_param_series = [
    stock_returns.rolling(window_size).apply(
        lambda x: CVaR_param(pd.DataFrame(x), alpha=alpha, dist="normal")
        ) for alpha in rolling_alphas
    ]

rolling_risk_measures = pd.concat(
    (
        VaR_hist_series +
        VaR_param_series +
        CVaR_hist_series +
        CVaR_param_series
        ),
    axis=1
    )

rolling_risk_measures.columns = [
    "VaR histórico 95%",
    "VaR histórico 99%",
    "VaR paramétrico 95%",
    "VaR paramétrico 99%",
    "CVaR histórico 95%",
    "CVaR histórico 99%",
    "CVaR paramétrico 95%",
    "CVaR paramétrico 99%"
    ]

rolling_risk_measures.dropna().head()

VaR histórico 95%  VaR histórico 99%  VaR paramétrico 95%  \
Date                                                                    
2011-01-06           0.030091           0.063572             0.037340   
2011-01-07           0.030091           0.063572             0.037275   
2011-01-10           0.030091           0.063572             0.037341   
2011-01-11           0.030091           0.063572             0.037383   
2011-01-12           0.030091           0.063572             0.037435   

            VaR paramétrico 99%  CVaR histórico 95%  CVaR histórico 99%  \
Date                                                                      
2011-01-06             0.053788            0.053769            0.088062   
2011-01-07             0.053776            0.053769            0.088062   
2011-01-10             0.053849            0.053769            0.088062   
2011-01-11             0.053882            0.053769            0.088062   
2011-01-12             0.053919            0.053769            0.088062   

            CVaR paramétrico 95%  CVaR paramétrico 99%  
Date                                                    
2011-01-06              0.063095              0.072928  
2011-01-07              0.063095              0.072928  
2011-01-10              0.063095              0.072928  
2011-01-11              0.063095              0.072928  
2011-01-12              0.063095              0.072928

#### Gráfica comparativa entre medidas de riesgo y retornos

In [40]:
risk_measures_and_returns = pd.merge(
    stock_returns,
    -rolling_risk_measures,
    left_index=True,
    right_index=True
    )

risk_measures_and_returns = risk_measures_and_returns * 100

fig = risk_measures_and_returns.plot(
    title=f"{ticker} - VaR y CVaR en media móvil de {window_size} días."
    )
fig.update_layout(xaxis_title="Fecha", yaxis_title="Retornos (%)")

### Evaluación de desempeño de las medidas de riesgo

#### Tabla comparativa

In [41]:
# Cantidad de violaciones de las medidas de riesgo
risk_measures_eval = (-rolling_risk_measures).gt(stock_returns[ticker], axis=0).sum()
risk_measures_eval = risk_measures_eval.to_frame('Núm. de violaciones')

# Porcentaje de violaciones de las medidas de riesgo
num_of_measures = len(rolling_risk_measures.dropna())
risk_measures_eval['Error (%)'] = (
    100 * risk_measures_eval['Núm. de violaciones'] / num_of_measures
    )

risk_measures_eval

Núm. de violaciones  Error (%)
VaR histórico 95%                     176   5.543307
VaR histórico 99%                      47   1.480315
VaR paramétrico 95%                   144   4.535433
VaR paramétrico 99%                    44   1.385827
CVaR histórico 95%                     65   2.047244
CVaR histórico 99%                     19   0.598425
CVaR paramétrico 95%                   50   1.574803
CVaR paramétrico 99%                   19   0.598425

### Gráfico comparativo con un nivel de referencia del 2.5%

In [47]:
fig = risk_measures_eval['Error (%)'].plot.bar(
    title=(
        f"{ticker} - Error porcentual de VaR y CVaR"
        f" históricos y paramétricos, en media móvil de {window_size} días."
        )
    )
fig.update_layout(
    xaxis_title="Medida de riesgo",
    yaxis_title="Error (%)"
    )
fig.add_shape(
    type="line",
    x0=-1,
    y0=2.5,
    x1=8,
    y1=2.5,
    line=dict(
        color="Red",
        width=2
    ),
    label = dict(
        text="2.5%",
        font=dict(
            color="Black",
            size=12
        )
    )
        
)


## Cálculo del VaR paramétrico normal con volatilidad móvil

$VaR_{1-\alpha} = q_\alpha \cdot \sigma_t^{252}$

In [43]:
def Var_volatility(returns_list, alpha):
    """Calcula el producto del VaR paramétrico normal a una confianza 1 - alpha
    por la volatilidad de los retornos.
    
    parameters
    ----------
    returns : list
        Lista de retornos.
    alpha : float
        Nivel de confianza: 1 - alpha.
        
    returns
    -------
    VaR_vol : float
        Producto del VaR paramétrico normal por la volatilidad.
    """ 
    returns_df = pd.DataFrame(returns_list)
    std = returns_df.std()
    
    VaR = VaR_param(returns_df, alpha=alpha, distribution="normal")
    VaR_vol = VaR * std
    
    return VaR_vol

In [44]:
VaR_vol_mov = [
    stock_returns.rolling(window_size).apply(
        lambda x: Var_volatility(x, alpha=alpha)
        ) for alpha in rolling_alphas
    ]

VaR_vol_series = pd.concat(VaR_vol_mov, axis=1)
VaR_vol_series.columns = [
    "VaR volatilidad móvil 95%",
    "VaR volatilidad móvil 99%"
    ]
VaR_vol_series.dropna().head()

/tmp/ipykernel_54283/1641923103.py:2: FutureWarning:

Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead



VaR volatilidad móvil 95%  VaR volatilidad móvil 99%
Date                                                            
2011-01-06                   0.000901                   0.001298
2011-01-07                   0.000903                   0.001302
2011-01-10                   0.000905                   0.001304
2011-01-11                   0.000905                   0.001305
2011-01-12                   0.000906                   0.001304